In [1]:
from __future__ import division

import pandas as pd
import numpy as np

import bokeh.plotting as bkP
import bokeh.models as bkM
from bokeh.palettes import Spectral6
from bokeh.embed import file_html
from bokeh.resources import CDN

from collections import namedtuple

bkP.output_notebook()
from bokeh.io import push_notebook


/Users/diaz/anaconda/lib/python2.7/site-packages/pandas/computation/__init__.py:19: UserWarning: The installed version of numexpr 2.4.4 is not supported in pandas and will be not be used

  UserWarning)


Loading BokehJS ...

### Glyphs

In [2]:
initRectGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.6,
            fill_color='gray')

undefinedGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.3,
            fill_color='gray')

selectedGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.6,
            fill_color='yellow')

saccadeGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.6,
            fill_color='green')

fixationGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.6,
            fill_color='red')


### Data sources and JS callbacks

In [3]:
undefinedSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))
fixSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))
sacSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))
purSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))

aSourceList = namedtuple('sourceList','undefined fixation saccade pursuit')

sourceList = aSourceList(undefined = undefinedSource, 
                       fixation = fixSource,
                       saccade = sacSource,
                       pursuit = purSource)

# Every box has a custom numerical ID
boxCounter = 0

boxCallback = bkM.CustomJS(args=dict(), code="""

        /// get BoxSelectTool dimensions from cb_data parameter of Callback
        var geometry = cb_data['geometry'];

        /// calculate Rect attributes
        var width = geometry['x1'] - geometry['x0'];
        var height = geometry['y1'] - geometry['y0'];
        var x = geometry['x0'] + width/2;
        var y = geometry['y0'] + height/2;
        
        var leftEdge = geometry['x0']
        var rightEdge = geometry['x1']
        
        var k = IPython.notebook.kernel
        
        k.execute("undefinedSource.data[\'x\'].append(" + x + ")");
        k.execute("undefinedSource.data[\'y\'].append(" + y + ")");
        k.execute("undefinedSource.data[\'width\'].append(" + width + ")");
        k.execute("undefinedSource.data[\'height\'].append(" + height + ")");
        k.execute("undefinedSource.data[\'leftEdge\'].append(" + leftEdge + ")");
        k.execute("undefinedSource.data[\'rightEdge\'].append(" + rightEdge + ")");
        k.execute("undefinedSource.data[\'boxID\'].append(boxCounter)");
        k.execute("boxCounter += 1");
        
        k.execute("push_notebook()");

    """)

selectedID = False
idx = False
boxIDs = False

# I need the boxID of the selected object
tapCallback = bkM.CustomJS(args=dict(uS = undefinedSource,fS=fixSource, sS=sacSource), code="""

        var idx = cb_obj.get('selected')['1d'].indices[0];
        var data = cb_obj.get('data');
        var boxIDs = data['boxID']
    
        
        if (typeof idx == 'undefined' || typeof boxIDs == 'undefined' ){
             
             console.log("Undefined values");
         }
         else{
         
            console.log("**IN**");
            console.log("  idx " + idx);
            console.log("  boxIDs " + cb_obj.get('data')['boxID']);
            
            IPython.notebook.kernel.execute("idx = " +  idx);
            IPython.notebook.kernel.execute("boxIDs = " +  boxIDs);
            
            if( Object.keys(boxIDs).length == 1 ){
                
                IPython.notebook.kernel.execute("selectedID = boxIDs");
            }
            else{
                console.log("  length " + Object.keys(boxIDs).length);
                IPython.notebook.kernel.execute("selectedID = boxIDs[idx]");
            }
            
         }
        
    """)

# ///var isEmpty = [];
# ///var inZeroD = {glyph: null, indices: isEmpty};
# ///idx = {0d: inZeroD,1d: var {indices: empty},2d: {'indices': empty}};



### Utility functions

In [4]:
def findParentSource(selectedID,sourceList):
    '''
    Returns the parent source of the 
    '''
    
    boxIDs_source = [source.data['boxID'] for source in sourceList]

    def find_in_list_of_list(mylist, char):
        for sub_list in mylist:
            if char in sub_list:
                return mylist.index(sub_list)
        return False

    sourceIdx = find_in_list_of_list(boxIDs_source, selectedID)

    if( sourceIdx is not False ):
        return sourceList[sourceIdx]
    else:
        return False
    
def moveBetweenSources(selectedID,currentSource,newSource):    
    
    # Get the index of the selected item in currSource
    valueIdx = currentSource.data['boxID'].index(selectedID)
        
    for key,values in currentSource.data.iteritems():
        
        # print currSource.data[key][valueIdx]
        newSource.data[key].append( currentSource.data[key][valueIdx] )
        del values[valueIdx]
        
    return newSource

### Callbacks for ipywidgets

In [5]:
def removeBox(sender):
    
    global selectedID
    global sourceList
    
    currentSource = findParentSource(selectedID,sourceList)
    
    #  Search sources and remove the offending entry
    for key,values in currentSource.data.iteritems():
        del values[currentSource.data['boxID'].index(selectedID)]
    
def labelEvent(sender):
    
    # This assumes that data for the selected event belongs to undefinedSource.
    # This may not be the case.
    global selectedID
    global sourceList
    
    if( selectedID is False):
        print 'ID not valid'
        return
        
    currentSource = findParentSource(selectedID,sourceList)
    
    if 'saccade' in sender.description:
        moveBetweenSources(selectedID,currentSource,sourceList.saccade)
    elif 'fixation' in sender.description:
        moveBetweenSources(selectedID,currentSource,sourceList.fixation)
    elif 'pursuit' in sender.description:
        moveBetweenSources(selectedID,currentSource,sourceList.pursuit)
    
    global idx, boxIDs
    print 'SelectedID: ' + str(selectedID) + ' is ' + str(boxIDs) + '[' + str(idx) + ']'
    boxIDs = idx = selectedID = False
    
    push_notebook()


###  ipywidgets

In [6]:

from ipywidgets import *
from IPython.display import display

b1 = Button(description='Label saccade',value=False)
b1.on_click(labelEvent)
b1.width = '20%'

b2 = Button(description='Label fixation',value=False)
b2.on_click(labelEvent)
b2.width = '20%'

b3 = Button(description='Remove event',value=False)
b3.on_click(removeBox)
b3.width = '20%'


### The figure

In [7]:
leftEdge = []
rightEdge = []

p = bkP.figure(width=800, height=350,x_range=[0,13], y_range=(0,2))

x = np.deg2rad(range(720))
y = 1+np.sin(x)

p.xaxis.axis_label = 'time'
p.yaxis.axis_label = 'position'

p.line(x,y,line_width=4,name='aLine')

undefinedSelectionGlyph = p.add_glyph(undefinedSource, initRectGlyph, 
                             selection_glyph= selectedGlyph, 
                             nonselection_glyph = undefinedGlyph,
                             name='undefined')

sacSelectionGlyph = p.add_glyph(sacSource, saccadeGlyph, 
                             selection_glyph=selectedGlyph, 
                             nonselection_glyph=saccadeGlyph,
                             name='saccade')

fixSelectionGlyph = p.add_glyph(fixSource, fixationGlyph, 
                             selection_glyph=selectedGlyph, 
                             nonselection_glyph=fixationGlyph,
                             name='fixation')

emptyRenderer = p.circle(x=1000,y=1000)
p.add_tools(bkM.BoxSelectTool(dimensions=["width"],callback=boxCallback,renderers=[emptyRenderer]))
p.add_tools(bkM.TapTool(callback=tapCallback))

bkP.show(p)


In [8]:
display(HBox([b1,b2,b3]))

SelectedID: 2 is (0, 1, 2)[2]
SelectedID: 1 is (0, 1)[1]
SelectedID: 0 is 0[0]
SelectedID: 2 is 2[0]
SelectedID: 1 is (1, 0, 2)[0]
SelectedID: 0 is (0, 2)[0]
SelectedID: 2 is 2[0]


In [9]:
print 'SelectedID: ' + str(selectedID) + ' is ' + str(boxIDs) + '[' + str(idx) + ']'

SelectedID: False is False[False]


In [10]:
undefinedSource.data

{'boxID': [],
 'height': [],
 'leftEdge': [],
 'rightEdge': [],
 'width': [],
 'x': [],
 'y': []}

In [11]:
sacSource.data

{'boxID': [],
 'height': [],
 'leftEdge': [],
 'rightEdge': [],
 'width': [],
 'x': [],
 'y': []}

In [12]:
# a = {'0d': {'glyph': None, 'indices': []},'1d': {'indices': []},'2d': {'indices': []}}
#fixSource.selected